In [1]:
from mnist.loader import MNIST
import numpy as np
import matplotlib.pyplot as plt
from util import *

In [2]:
# 0:discrete / 1:continuous
mode = 1

In [3]:
mndata = MNIST('./data')
mndata.gz = True
images,labels = mndata.load_training()
test_images,test_labels = mndata.load_testing()
images = np.array(images)

In [4]:
# get prior
labels = np.array(labels)
prior = get_prior(labels)

In [5]:
if mode == 0:
    # for train
    discrete_bins = np.zeros((10, 28*28, 32))
    for img in range(len(images)):
        c = labels[img]
        for d in range(28*28):
            #print(int(images[img][d])//8)
            discrete_bins[c, d, int(images[img][d])//8] += 1  #每8個gray level分一個bin
    for c in range(10):
        for d in range(28*28):
            count = 0
            for bin in range(32):
                count += discrete_bins[c][d][bin]
            discrete_bins[c][d][:] /= count   #conditional probability of every bin
    # for test
    error_cnt = 0
    for img in range(len(test_images)):
        probs = np.zeros(10)
        for p in range(10):
            for d in range(28*28):
                # value相乘 = log相加
                probs[p] += np.log(max(1e-4, discrete_bins[p, d, test_images[img][d]//8]))
                # 避免log 0的情況 (1/60000 大概是1e-4)
            probs[p] += np.log(prior[p])

        probs /= np.sum(probs)
        print('Posterior (in log scale):')
        for c in range(10):
            print('{}: {}'.format(c, probs[c]))
        predict=np.argmin(probs)  # np.sum是negative，所以這裡取min
        print('Prediction: {}, Ans: {}'.format(predict, test_labels[img]))
        print()
        if predict != test_labels[img]:
            error_cnt += 1
    
    # Imagination of numbers in Bayesian classifier:
    print_imagination_number(discrete_bins, 16)
    print('Error rate: {:.4f}'.format(error_cnt / len(test_images)))


elif mode == 1:
    continuous_prob = np.zeros((10, 28*28, 256))
    # for train
    epsilon_var = 1000  #設一個variance threshold，避免likelihood過小，以至於訓練結果不佳
    
    for c in range(10):
        A = images[labels==c]
        for d in range(28*28):
            mu = np.mean(A[:, d])
            var = get_variance(A[:, d], epsilon_var)  #避免var是0
            for j in range(256):
                continuous_prob[c, d, j] = gaussain_prob(j, mu, var)
    # for test
    error_cnt = 0
    for img in range(len(test_images)):
        probs = np.zeros(10)
        for c in range(10):
            for d in range(28*28):
                probs[c] += np.log(max(1e-30, continuous_prob[c, d, test_images[img][d]]))
                # 避免continuous_prob太小log算不出來(實驗結果:越小越好)
            probs[c] += np.log(prior[c])
        # for normalized
        probs /= np.sum(probs)
        print('Posterior (in log scale):')
        for c in range(10):
            print('{}: {}'.format(c, probs[c]))
        predict=np.argmin(probs)
        print('Prediction: {}, Ans: {}'.format(predict, test_labels[img]))
        print()
        if predict != test_labels[img]:
            error_cnt += 1
    print_imagination_number(continuous_prob, 128)
    print('Error rate: {:.4f}'.format(error_cnt / len(test_images)))
    print()

Posterior (in log scale):
0: 0.10163954560704286
1: 0.11185545952217765
2: 0.1018820432163266
3: 0.0981050773889677
4: 0.09721318504610796
5: 0.09851801533113187
6: 0.10634315564461946
7: 0.09140445213171912
8: 0.09835884263659952
9: 0.09468022347530718
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.09704621692406198
1: 0.10825159588397085
2: 0.0888713049638427
3: 0.09338460300934037
4: 0.10491205923626079
5: 0.09545161045080865
6: 0.09260843774925902
7: 0.1142388174447095
8: 0.09636162814811894
9: 0.10887372618962715
Prediction: 2, Ans: 2

Posterior (in log scale):
0: 0.10735972088443224
1: 0.0924581901552266
2: 0.10001131489917355
3: 0.1001850757663198
4: 0.10017868723400189
5: 0.09957654241478579
6: 0.10035782077926585
7: 0.1002936276038355
8: 0.09949556759813076
9: 0.10008345266482793
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.09003326282860324
1: 0.1316211891558214
2: 0.09614085553091817
3: 0.09640163431393185
4: 0.09834919464576272
5: 0.09478316061705355
6: 0.09

Posterior (in log scale):
0: 0.09198395220544413
1: 0.1138268279012592
2: 0.0895261322523932
3: 0.09264327141311687
4: 0.10382214282691571
5: 0.0926232821018158
6: 0.1002231278929937
7: 0.11197758415154642
8: 0.09203883069770558
9: 0.11133484855680945
Prediction: 2, Ans: 2

Posterior (in log scale):
0: 0.10137488843527452
1: 0.11480482673190598
2: 0.1001531150455129
3: 0.09866933878835565
4: 0.09639868003105655
5: 0.09926605935779585
6: 0.10390625442999608
7: 0.0915763081041825
8: 0.09838193138232648
9: 0.09546859769359343
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.10945554223817623
1: 0.0928302757057271
2: 0.10151118978139587
3: 0.09954624827082344
4: 0.09987439845121694
5: 0.0988323328833829
6: 0.10069609498679964
7: 0.09974539665132488
8: 0.09878253605222394
9: 0.09872598497892902
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.09884289787720901
1: 0.10185878656832119
2: 0.09651605742981877
3: 0.09643807363191427
4: 0.10347506743269388
5: 0.09682132919154166
6: 0.09

Posterior (in log scale):
0: 0.10750142538890953
1: 0.10953168017411946
2: 0.09983866444559693
3: 0.09758256119616869
4: 0.09614718595404709
5: 0.09729027121043864
6: 0.09910988407087812
7: 0.09782867201654352
8: 0.09752423122837783
9: 0.09764542431492018
Prediction: 4, Ans: 7

Posterior (in log scale):
0: 0.09641973813994241
1: 0.11433928160404698
2: 0.09573280448679455
3: 0.09897445695923683
4: 0.09927815843674925
5: 0.09614138994221039
6: 0.09256705753273077
7: 0.10714960968230003
8: 0.09678693473309982
9: 0.10261056848288895
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.1059581199365449
1: 0.1269576006854585
2: 0.09942039497187724
3: 0.09985221916972259
4: 0.0923167763666755
5: 0.09640970604515844
6: 0.09900887372267493
7: 0.09420080605233104
8: 0.09574188813118388
9: 0.09013361491837306
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.10127000070442894
1: 0.11012215037871997
2: 0.09694094779609749
3: 0.0999028126620601
4: 0.09764204577411678
5: 0.09963237443997425
6: 

Posterior (in log scale):
0: 0.10759762259100603
1: 0.09364259974152375
2: 0.10068295801262477
3: 0.09990432685179282
4: 0.10032813148982586
5: 0.09954572086961135
6: 0.10008378169318717
7: 0.09933678144187638
8: 0.09987221428357405
9: 0.09900586302497776
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.10116929809601623
1: 0.11255007891424228
2: 0.09988842208993871
3: 0.09790589588794399
4: 0.09660505174854245
5: 0.09155726866762384
6: 0.10069101017010171
7: 0.1044196845225198
8: 0.09397057823587376
9: 0.10124271166719709
Prediction: 5, Ans: 5

Posterior (in log scale):
0: 0.0980440452828482
1: 0.12374586958728234
2: 0.09612578037069101
3: 0.09838398065627658
4: 0.09520219890420172
5: 0.09733126479301261
6: 0.09168270178832746
7: 0.10000898748055724
8: 0.09960390067687343
9: 0.09987127045992926
Prediction: 6, Ans: 6

Posterior (in log scale):
0: 0.09577890784503966
1: 0.12202495584833921
2: 0.09836745654494117
3: 0.09771093414869617
4: 0.09739368291373875
5: 0.09701057247054218
6

Posterior (in log scale):
0: 0.10032576829506616
1: 0.10369912892969185
2: 0.10292192256827884
3: 0.09875140274755313
4: 0.09836341123164023
5: 0.09660104813309776
6: 0.10739396218957208
7: 0.09734702849693762
8: 0.09715604924076263
9: 0.09744027816739968
Prediction: 5, Ans: 5

Posterior (in log scale):
0: 0.10344101948297717
1: 0.12968716483935172
2: 0.09900190862549789
3: 0.09808349425268786
4: 0.0919599468504604
5: 0.09452849357592859
6: 0.09869661136878978
7: 0.09874091791239181
8: 0.09574500344929249
9: 0.09011543964262228
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.10709725896979917
1: 0.09650988693135772
2: 0.10022666870660024
3: 0.09751684149348998
4: 0.0991961929877815
5: 0.09841800765743511
6: 0.10292073076466056
7: 0.10066127052099019
8: 0.09833890926131733
9: 0.0991142327065683
Prediction: 1, Ans: 3

Posterior (in log scale):
0: 0.10806494223642504
1: 0.11871168200712943
2: 0.10175858351150413
3: 0.09714337224122466
4: 0.09372174766135109
5: 0.09587036851032969
6:

...

Posterior (in log scale):
0: 0.0880985842858591
1: 0.12600726667659826
2: 0.09855313374184317
3: 0.09155981895669826
4: 0.10020280175987685
5: 0.0897504527330245
6: 0.10650434079104996
7: 0.1035449648420391
8: 0.09294232270086203
9: 0.10283631351214863
Prediction: 0, Ans: 5

Posterior (in log scale):
0: 0.09486004845126322
1: 0.12201247670895832
2: 0.09334992974588387
3: 0.0964245224899739
4: 0.09724943437534703
5: 0.0912453833462475
6: 0.09177075782548567
7: 0.1102695936575303
8: 0.09718805753555532
9: 0.10562979586375507
Prediction: 5, Ans: 6

Posterior (in log scale):
0: 0.1063554958948493
1: 0.10580845567061815
2: 0.10129872841320042
3: 0.10010537745970069
4: 0.09827035122424592
5: 0.0981238031856383
6: 0.10554266189469778
7: 0.09246410311926316
8: 0.09668880472484037
9: 0.09534221841294592
Prediction: 7, Ans: 7

Posterior (in log scale):
0: 0.10025713888542279
1: 0.10427699584401526
2: 0.09552453243385362
3: 0.09583552153168921
4: 0.10163614207399953
5: 0.0937695804963392
6: 0.107

Posterior (in log scale):
0: 0.09214221846663617
1: 0.11697423154777013
2: 0.09077693349032871
3: 0.09652744151738529
4: 0.09961218149728032
5: 0.0959619725872651
6: 0.10200545674679515
7: 0.10541847555323854
8: 0.0961398835495729
9: 0.10444120504372763
Prediction: 2, Ans: 2

Posterior (in log scale):
0: 0.10677502623754935
1: 0.0926855622021356
2: 0.09591737731911644
3: 0.09643970170853071
4: 0.10211827197284867
5: 0.09676969504251118
6: 0.10584983912003751
7: 0.103660275025369
8: 0.09523966890045811
9: 0.10454458247144352
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.0879616737883601
1: 0.12078210750858732
2: 0.09470706081952388
3: 0.09999278826101393
4: 0.09839266213191485
5: 0.09480673389778879
6: 0.10099979674590283
7: 0.10202816389868603
8: 0.09797322308815408
9: 0.10235578986006821
Prediction: 0, Ans: 0

Posterior (in log scale):
0: 0.08152691319966691
1: 0.12724412172192778
2: 0.0971977846230492
3: 0.09591308286160066
4: 0.09869939344520912
5: 0.08768898498374336
6: 0.1

Posterior (in log scale):
0: 0.10893395715450702
1: 0.09214295487915021
2: 0.09962246805758752
3: 0.09962603372034827
4: 0.09956559050328169
5: 0.09898144038122039
6: 0.1030827109977714
7: 0.10004862526454161
8: 0.09808148545216508
9: 0.09991473358942675
Prediction: 1, Ans: 1

Posterior (in log scale):
0: 0.10040443476890328
1: 0.10107205546618865
2: 0.09761851887163714
3: 0.09864112174313411
4: 0.1010754463032509
5: 0.09741511094082607
6: 0.09917290564222823
7: 0.10454643708578187
8: 0.09687049697298028
9: 0.10318347220506964
Prediction: 8, Ans: 0

Posterior (in log scale):
0: 0.10427343016669134
1: 0.09280054654402957
2: 0.09562113669712616
3: 0.09643175638743304
4: 0.1040792806368801
5: 0.09684307151287427
6: 0.10118895649923787
7: 0.10824116255395648
8: 0.09471841799905893
9: 0.10580224100271245
Prediction: 1, Ans: 2

Posterior (in log scale):
0: 0.10064993091747464
1: 0.10056636285676068
2: 0.0994315270570632
3: 0.09620128361947557
4: 0.10212189602113593
5: 0.09696023145000764
6: 

Posterior (in log scale):
0: 0.10119758393127748
1: 0.11045620253994544
2: 0.0982217203492274
3: 0.09519080673405589
4: 0.09854907785562701
5: 0.09362833696797479
6: 0.10872325963188147
7: 0.10117838167450474
8: 0.0931797717174675
9: 0.0996748585980382
Prediction: 8, Ans: 3

Posterior (in log scale):
0: 0.10389486665867712
1: 0.11285303612932102
2: 0.10375741665145058
3: 0.09829925777877407
4: 0.09530207608132886
5: 0.09466276674079369
6: 0.10864303432086174
7: 0.09475559728249455
8: 0.09331379432517277
9: 0.09451815403112582
Prediction: 8, Ans: 3

Posterior (in log scale):
0: 0.1033628357192043
1: 0.11350683018022736
2: 0.10210523244785866
3: 0.10046511083015365
4: 0.09293420298244191
5: 0.09580164356860003
6: 0.10483901357101236
7: 0.0970420375784779
8: 0.09771041392774271
9: 0.09223267919428109
Prediction: 9, Ans: 9

Posterior (in log scale):
0: 0.10811983210286237
1: 0.09190528733526726
2: 0.10034364151104855
3: 0.0988244997124272
4: 0.10100678855041224
5: 0.09847288592888723
6: 0.

0 0 0 0 0 0 0 0 0 0 1 1 1 1 1 0 0 0 1 1 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 
0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 0 1 1 0 0 0 0 0 0 0 
0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 
0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 1 1 0 0 1 1 1 1 1 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 
0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0